In [1]:
%matplotlib inline
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np

# Estimation de la latence et de la capacité d’une connexion à partir de mesures asymétriques

Un modèle simple et fréquemment utilisé pour décrire la performance d'une connexion de réseau consiste à supposer que le temps d'envoi T pour un message dépend principalement de sa taille S (nombre d'octets) et de deux grandeurs propres à la connexion : la latence L (en secondes) et la capacité C (en octets/seconde). La relation entre ces quatre quantités est ___T(S) = L + S/C___. Ce modèle néglige un grand nombre de détails. D'une part, L et C dépendent bien sûr du protocole de communication choisi mais aussi dans une certaine mesure de S. D'autre part, la mesure de T(S) comporte en général une forte composante aléatoire. Nous nous intéressons ici au temps moyen qu'il faut pour envoyer un message d'une taille donnée.

Nous allons estimer L et C à partir d'une série d'observations de T pour des valeurs différentes de S. Notre analyse commence avec la lectures des données brutes, disponibles pour deux connexions différentes, qui ont été obtenues avec l'outil ping.

Les deux fichiers contiennent la sortie brute de l'outil ping qui a été exécuté dans une boucle en variant de façon aléatoire la taille du message. Chaque ligne a la forme suivante:

__[1421761682.052172] 665 bytes from lig-publig.imag.fr (129.88.11.7): icmp_seq=1 ttl=60 time=22.5 ms__

Au début, entre crochet, nous trouvons la date à laquelle la mesure a été prise, exprimée en secondes depuis le 1er janvier 1970. La taille du message en octets est donnée juste après, suivie par le nom de la machine cible et son adresse IP, qui sont normalement identiques pour toutes les lignes à l'intérieur d'un jeu de données. À la fin de la ligne, nous trouvons le temps d'envoi (aller-retour) en millisecondes. Les autres indications, icmp_seq et ttl, n'ont pas d'importance pour notre analyse

# 1er jeu de données

Nous commencons par travailler sur le 1er jeu de données qui examine une connexion courte à l'intérieur d'un campus.

Nous lisons le fichiers et récupérons les données intérésantes : la date (convertie de secondes à année-mois-jour), la taille des messages, la machine cible et les adresses IP. Nous gardons aussi le temps de transmission, si celui-ci n'est pas présent la ligne n'est pas gardée. Les données sont ensuite triées en fonction de la date.

In [2]:
fichier_1 = open("liglab2.log").readlines()
fichier_1 = [l for l in fichier_1 if 'time' in l]
raw_data = [l.split(' ') for l in fichier_1]
data = [ [d[0][1:-1], int(d[1]), d[4], d[5][1:-2], d[8].split('=')[1]] for d in raw_data]
data = pd.DataFrame(data, columns=['date', 'taille', 'cible', 'IP', 'temps'])
data['date'] = pd.to_datetime(data['date'], unit='s')
sorted_data = data.set_index('date').sort_index()
sorted_data

taille               cible           IP temps
date                                                                     
2015-01-20 13:48:02.052172     665  lig-publig.imag.fr  129.88.11.7  22.5
2015-01-20 13:48:02.277315    1373  lig-publig.imag.fr  129.88.11.7  21.2
2015-01-20 13:48:02.502054     262  lig-publig.imag.fr  129.88.11.7  21.2
2015-01-20 13:48:02.729257    1107  lig-publig.imag.fr  129.88.11.7  23.3
2015-01-20 13:48:02.934648    1128  lig-publig.imag.fr  129.88.11.7  1.41
2015-01-20 13:48:03.160397     489  lig-publig.imag.fr  129.88.11.7  21.9
2015-01-20 13:48:03.443055    1759  lig-publig.imag.fr  129.88.11.7  78.7
2015-01-20 13:48:03.672157    1146  lig-publig.imag.fr  129.88.11.7  25.1
2015-01-20 13:48:03.899933     884  lig-publig.imag.fr  129.88.11.7  24.0
2015-01-20 13:48:04.122687    1422  lig-publig.imag.fr  129.88.11.7  19.5
2015-01-20 13:48:04.344135    1180  lig-publig.imag.fr  129.88.11.7  18.0
2015-01-20 13:48:04.566271     999  lig-publig.imag.fr  129.88.11.7  18.8
2015-01-20 13:48:04.998504    1020  lig-publig.imag.fr  129.88.11.7  24.3
2015-01-20 13:48:05.205172      71  lig-publig.imag.fr  129.88.11.7  3.45
2015-01-20 13:48:05.414106      34  lig-publig.imag.fr  129.88.11.7  5.85
2015-01-20 13:48:05.620117    1843  lig-publig.imag.fr  129.88.11.7  2.31
2015-01-20 13:48:05.824949     407  lig-publig.imag.fr  129.88.11.7  1.14
2015-01-20 13:48:06.029177     356  lig-publig.imag.fr  129.88.11.7  1.10
2015-01-20 13:48:06.234464    1511  lig-publig.imag.fr  129.88.11.7  2.18
2015-01-20 13:48:06.438772     587  lig-publig.imag.fr  129.88.11.7  1.27
2015-01-20 13:48:06.643208     809  lig-publig.imag.fr  129.88.11.7  1.33
2015-01-20 13:48:06.848323    1364  lig-publig.imag.fr  129.88.11.7  1.51
2015-01-20 13:48:07.053400    1153  lig-publig.imag.fr  129.88.11.7  1.44
2015-01-20 13:48:07.257704     853  lig-publig.imag.fr  129.88.11.7  1.30
2015-01-20 13:48:07.463275    1510  lig-publig.imag.fr  129.88.11.7  2.17
2015-01-20 13:48:07.668423     123  lig-publig.imag.fr  129.88.11.7  1.21
2015-01-20 13:48:07.874230    1966  lig-publig.imag.fr  129.88.11.7  2.20
2015-01-20 13:48:08.078667     933  lig-publig.imag.fr  129.88.11.7  1.34
2015-01-20 13:48:08.283655     922  lig-publig.imag.fr  129.88.11.7  1.42
2015-01-20 13:48:08.488688      24  lig-publig.imag.fr  129.88.11.7  1.12
...                            ...                 ...          ...   ...
2015-01-20 16:26:20.743715    1772  lig-publig.imag.fr  129.88.11.7  28.8
2015-01-20 16:26:20.949053      41  lig-publig.imag.fr  129.88.11.7  1.14
2015-01-20 16:26:21.155685    1944  lig-publig.imag.fr  129.88.11.7  2.32
2015-01-20 16:26:21.362095     400  lig-publig.imag.fr  129.88.11.7  1.98
2015-01-20 16:26:21.569409     226  lig-publig.imag.fr  129.88.11.7  3.01
2015-01-20 16:26:21.780805     466  lig-publig.imag.fr  129.88.11.7  7.45
2015-01-20 16:26:21.998869     350  lig-publig.imag.fr  129.88.11.7  13.5
2015-01-20 16:26:22.248969    1829  lig-publig.imag.fr  129.88.11.7  45.9
2015-01-20 16:26:22.512386    1954  lig-publig.imag.fr  129.88.11.7  58.5
2015-01-20 16:26:22.717961    1074  lig-publig.imag.fr  129.88.11.7  1.45
2015-01-20 16:26:22.923292      46  lig-publig.imag.fr  129.88.11.7  1.11
2015-01-20 16:26:23.129965    1844  lig-publig.imag.fr  129.88.11.7  2.26
2015-01-20 16:26:23.335449     645  lig-publig.imag.fr  129.88.11.7  1.24
2015-01-20 16:26:23.540901     444  lig-publig.imag.fr  129.88.11.7  1.25
2015-01-20 16:26:23.747983    1940  lig-publig.imag.fr  129.88.11.7  2.46
2015-01-20 16:26:23.954099    1411  lig-publig.imag.fr  129.88.11.7  1.47
2015-01-20 16:26:24.159879      49  lig-publig.imag.fr  129.88.11.7  1.21
2015-01-20 16:26:24.365815     420  lig-publig.imag.fr  129.88.11.7  1.55
2015-01-20 16:26:24.571516     227  lig-publig.imag.fr  129.88.11.7  1.22
2015-01-20 16:26:24.777325     947  lig-publig.imag.fr  129.88.11.7  1.34
2015-01-20 16:26:24.983905    1960  lig-publig.imag.fr  129.88.11.7  2.43
2015-01-20 16:26:25.188976     5

Nous vérfions que toutes les données proviennents de la même machine cible. Ici pas de problème.

In [3]:
sorted_data['cible'].value_counts()

lig-publig.imag.fr    44036
Name: cible, dtype: int64

In [4]:
sorted_data['IP'].value_counts()

129.88.11.7    44036
Name: IP, dtype: int64